<a href="https://colab.research.google.com/github/rupam1123/Enviromental_Sound_Classification_Deep-Learning-Group-soundify-/blob/main/training.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [5]:
import os
import sys
import pickle
import copy
from datetime import datetime
from tqdm import tqdm
import numpy as np
import pandas as pd
import seaborn as sns
import torch
import torch.nn.functional as F
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms
import matplotlib.pyplot as plt
%matplotlib inline

In [72]:
from google.colab import drive
drive.mount('/content/drive')
dataset_path = "/content/drive/My Drive/UrbanSound8K/UrbanSound8K"
print(os.listdir(dataset_path))
print("success")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
['.DS_Store', 'FREESOUNDCREDITS.txt', 'UrbanSound8K_README.txt', 'audio', 'metadata', 'extracted_features.pkl']
success


In [13]:
import os
import pickle
file_path = os.path.join("/content/drive/My Drive/UrbanSound8K/UrbanSound8K", "extracted_features.pkl")
try:
    with open(file_path, "rb") as f:
       e = pickle.load(f)
    print(e)
except FileNotFoundError:
    print(f"Error: File not found at path: {file_path}")

[[array([-217.35526   ,   70.22338   , -130.38527   ,  -53.282898  ,
        -21.19913   ,  -22.677624  ,  -10.855971  ,   18.294256  ,
          6.6527033 ,   14.324025  ,  -12.167682  ,    2.276837  ,
        -17.779192  ,   10.388951  ,   -6.5828357 ,   -0.69445676,
        -18.336023  ,    1.994253  ,   -5.143332  ,    8.3024    ,
        -12.645056  ,   -6.5297318 ,    4.617667  ,   -2.1799169 ,
         -6.662824  ,    0.35971096,   -3.9084103 ,    4.7756243 ,
         -6.3845215 ,   -5.3798175 ,    0.9159778 ,    6.970493  ,
         -0.24866785,    1.6782194 ,   -5.6111803 ,   -2.9643462 ,
          3.1490579 ,   -1.6930531 ,   -0.61698425,    0.38600534],
      dtype=float32), 'dog_bark'], [array([-4.2409818e+02,  1.0934077e+02, -5.2919525e+01,  6.0864750e+01,
        2.4529248e-01,  1.7347328e+01,  2.0955825e+00,  1.0712965e+01,
       -1.3986130e+00,  1.2310798e+01, -1.1208863e+01,  2.1075323e+01,
       -9.4902792e+00,  1.3526470e+01, -2.3910522e-01,  7.1590004e+00,
       

In [45]:
### Split the dataset into independent and dependent dataset

e_df = pd.DataFrame(e, columns=["feature", "class"])
# as e was a list so we convert into a dataframe
X=np.array(e_df['feature'].tolist())
y=np.array(e_df['class'].tolist())

In [46]:
X.shape

(7970, 40)

In [47]:
y,"and",y.shape

(array(['dog_bark', 'children_playing', 'children_playing', ...,
        'car_horn', 'car_horn', 'car_horn'], dtype='<U16'),
 'and',
 (7970,))

In [53]:
print("y shape:", y.shape)
print("y data type:", type(y))
print(y[:2])  # Print first 10 values


y shape: (7970, 10)
y data type: <class 'numpy.ndarray'>
[[False False False  True False False False False False False]
 [False False  True False False False False False False False]]


In [55]:
### Train Test Split
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(X,y,test_size=0.2,random_state=0)

# here 20% of the dataset will be used for testing

In [56]:
print("Training set size:", X_train.shape, y_train.shape)
print("Testing set size:", X_test.shape, y_test.shape)

Training set size: (6376, 40) (6376, 10)
Testing set size: (1594, 40) (1594, 10)


In [57]:
"success"

'success'

# ANN Model

In [58]:
import tensorflow as tf
print(tf.__version__)

2.18.0


In [59]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense,Dropout,Activation,Flatten
from tensorflow.keras.optimizers import Adam
from sklearn import metrics

In [64]:
### No of classes
num_labels=y.shape[1]
" total classes ::: ",num_labels

(' total classes ::: ', 10)

In [65]:
# Instead of just calling Dense() without arguments, specify the number of units:
Dense(units=64)  # Replace 64 with the desired number of units for this layer

<Dense name=dense_1, built=False>

In [66]:
# ANN

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, Dropout, BatchNormalization

model = Sequential()

### First Layer
model.add(Dense(512, input_shape=(40,)))
model.add(Activation('relu'))
model.add(BatchNormalization())
model.add(Dropout(0.5))

### Second Layer
model.add(Dense(1024))
model.add(Activation('relu'))
model.add(BatchNormalization())
model.add(Dropout(0.5))

### Third Layer
model.add(Dense(512))
model.add(Activation('relu'))
model.add(BatchNormalization())
model.add(Dropout(0.5))

### Fourth Layer
model.add(Dense(256))
model.add(Activation('relu'))
model.add(BatchNormalization())
model.add(Dropout(0.5))

### Final Layer
model.add(Dense(num_labels))
model.add(Activation('softmax'))


/usr/local/lib/python3.11/dist-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [67]:
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ dense_2 (Dense)                      │ (None, 512)                 │          20,992 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation (Activation)              │ (None, 512)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization                  │ (None, 512)                 │           2,048 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout (Dropout)                    │ (None, 512)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_3 (Dense)                      │ (None, 1024)                │         525,312 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation_1 (Activation)            │ (None, 1024)                │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_1                │ (None, 1024)                │           4,096 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_1 (Dropout)                  │ (None, 1024)                │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_4 (Dense)                      │ (None, 512)                 │         524,800 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation_2 (Activation)            │ (None, 512)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_2                │ (None, 512)                 │           2,048 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_2 (Dropout)                  │ (None, 512)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_5 (Dense)                      │ (None, 256)                 │         131,328 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation_3 (Activation)            │ (None, 256)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ batch_normalization_3                │ (None, 256)                 │           1,024 │
│ (BatchNormalization)                 │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_3 (Dropout)                  │ (None, 256)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_6 (Dense)                      │ (None, 10)                  │           2,570 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ activation_4 (Activation)            │ (None, 10)                  │               0 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 1,214,218 (4.63 MB)

 Trainable params: 1,209,610 (4.61 MB)

 Non-trainable params: 4,608 (18.00 KB)

In [68]:
from tensorflow.keras.optimizers import Adam

model.compile(
    optimizer=Adam(learning_rate=0.0001),  # Lower learning rate for better convergence
    loss='categorical_crossentropy',  # Suitable for multi-class classification
    metrics=['accuracy']
)


In [69]:
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping, ReduceLROnPlateau, TensorBoard
from datetime import datetime
import os
num_epochs = 200
num_batch_size = 20
checkpointer = ModelCheckpoint(filepath='saved_models/audio_classification_best.keras',
                               verbose=1, save_best_only=True)

early_stopping = EarlyStopping(monitor='val_loss',
                               patience=5,
                               restore_best_weights=True,
                               verbose=1)

lr_scheduler = ReduceLROnPlateau(monitor='val_loss',
                                  factor=0.5,
                                  patience=3,
                                  min_lr=1e-6,
                                  verbose=1)
log_dir = "logs/fit/" + datetime.now().strftime("%Y%m%d-%H%M%S")
tensorboard_callback = TensorBoard(log_dir=log_dir, histogram_freq=1)

start = datetime.now()
# Train the model
model.fit(X_train, y_train,
          batch_size=num_batch_size,
          epochs=num_epochs,
          validation_data=(X_test, y_test),
          callbacks=[checkpointer, early_stopping, lr_scheduler, tensorboard_callback],
          verbose=1)

duration = datetime.now() - start
print("Training completed in time: ", duration)


Epoch 1/200
318/319 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - accuracy: 0.1544 - loss: 3.2439
Epoch 1: val_loss improved from inf to 1.73761, saving model to saved_models/audio_classification_best.keras
319/319 ━━━━━━━━━━━━━━━━━━━━ 14s 28ms/step - accuracy: 0.1546 - loss: 3.2427 - val_accuracy: 0.3959 - val_loss: 1.7376 - learning_rate: 1.0000e-04
Epoch 2/200
319/319 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step - accuracy: 0.2540 - loss: 2.6517
Epoch 2: val_loss improved from 1.73761 to 1.57182, saving model to saved_models/audio_classification_best.keras
319/319 ━━━━━━━━━━━━━━━━━━━━ 12s 34ms/step - accuracy: 0.2541 - loss: 2.6514 - val_accuracy: 0.4479 - val_loss: 1.5718 - learning_rate: 1.0000e-04
Epoch 3/200
319/319 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - accuracy: 0.3106 - loss: 2.3282
Epoch 3: val_loss improved from 1.57182 to 1.49724, saving model to saved_models/audio_classification_best.keras
319/319 ━━━━━━━━━━━━━━━━━━━━ 7s 23ms/step - accuracy: 0.3106 - loss: 2.3281 - val_accuracy: 0.4711 - val_lo

In [71]:
test_accuracy=model.evaluate(X_test,y_test,verbose=0)
print(test_accuracy[1]*100,'%')

89.02133107185364 %
